# Divvy Bike Data Lakehouse Project
## 1. Ingesting Raw Data `Bronze Layer`
In this step, we read the raw CSV files from DBFS and write them into Delta format.

In [0]:
from pyspark.sql.types import StructType, StructField, StringType, IntegerType, TimestampType, BooleanType, FloatType, DateType

# Rider schema
rider_schema = StructType([
    StructField("rider_id", IntegerType(), True),
    StructField("first_name", StringType(), True),
    StructField("last_name", StringType(), True),
    StructField("address", StringType(), True),
    StructField("birthday", TimestampType(), True),            # was DateType
    StructField("account_start_date", DateType(), True),  # was DateType
    StructField("account_end_date", DateType(), True),    # was DateType
    StructField("is_member", BooleanType(), True)
])

# Trip schema
trip_schema = StructType([
    StructField("trip_id", StringType(), True),
    StructField("rideable_type", StringType(), True),
    StructField("started_at", TimestampType(), True),
    StructField("ended_at", TimestampType(), True),
    StructField("start_station_id", StringType(), True),
    StructField("end_station_id", StringType(), True),
    StructField("rider_id", IntegerType(), True),
])

# Station schema
station_schema = StructType([
    StructField("station_id", StringType(), True),
    StructField("name", StringType(), True),              
    StructField("latitude", FloatType(), True),    
    StructField("longitude", FloatType(), True),
])

# Payment schema
payment_schema = StructType([
    StructField("payment_id", IntegerType(), True),         
    StructField("date", TimestampType(), True),      
    StructField("amount", FloatType(), True),
    StructField("rider_id", IntegerType(), True),                 
])

# Dictionary mapping
filesPath = {
    "rider": ["dbfs:/FileStore/projectDatalake/riders.csv", rider_schema],
    "trip": ["dbfs:/FileStore/projectDatalake/trips.csv", trip_schema],
    "station": ["dbfs:/FileStore/projectDatalake/stations.csv", station_schema],
    "payment": ["dbfs:/FileStore/projectDatalake/payments.csv", payment_schema]
}


for name, (path,schema) in filesPath.items():
    df = (spark.read.format("csv")
          .option("header", "true")
          .schema(schema)
          .load(path))
    
    # Save as Delta table
    df.write.format("delta").mode("overwrite").save(f"/deltaLake/bronze/{name}")
    
    # Verify by displaying first rows
    display(spark.read.format("delta").load(f"/deltaLake/bronze/{name}"))


rider_id first_name last_name address birthday account_start_date account_end_date is_member 23344 Curtis Harris 0309 Cassie Fall Suite 266 1979-12-13T00:00:00Z 2019-06-09 null true 23345 Joshua Farmer 55226 Brandon Forge Apt. 718 1990-07-25T00:00:00Z 2020-10-16 2021-07-01 true 23346 Jill Rangel 616 Maurice Forges Suite 888 1988-03-26T00:00:00Z 2021-01-10 null true 23347 Jamie Evans 33245 Shane Walks 1973-10-10T00:00:00Z 2019-01-16 2021-03-01 true 23348 Shirley Gomez 57751 English Lake 2004-01-22T00:00:00Z 2020-02-01 null true 23349 Michael Schultz 976 Tracy Rest 1986-11-05T00:00:00Z 2016-03-06 2017-03-01 true 23350 Nathan Baker 554 Audrey Glen Apt. 976 1984-10-12T00:00:00Z 2013-05-03 null true 23351 Shaun Casey 886 Joanna Unions 1990-11-07T00:00:00Z 2014-03-23 null false 23352 Jennifer Day 3731 Hayes Rest Apt. 371 1994-08-18T00:00:00Z 2019-05-05 2021-10-01 true 23353 Troy Gross 93349 Joshua Bridge 1962-12-08T00:00:00Z 2018-09-27 null true 23354 Christopher Henry 99065 Robert Tunnel 1988-07-18T00:00:00Z 2015-03-18 null true 23355 Lindsay Morgan 25870 Brown Mountains 1994-04-25T00:00:00Z 2020-07-30 null true 23356 Rebecca Hawkins 373 Amanda Fort 2005-03-04T00:00:00Z 2019-09-03 null true 23357 Christopher Ruiz 452 Christopher Gateway 1998-05-19T00:00:00Z 2016-05-25 null true 23358 Seth Hernandez 8234 Katherine Brooks Apt. 869 2003-08-08T00:00:00Z 2020-01-25 null true 23359 Megan Mills 2454 White Avenue Apt. 550 1982-02-16T00:00:00Z 2020-01-27 null true 23360 Charles Howell 2218 Michelle Crossroad Suite 327 1982-08-14T00:00:00Z 2021-08-28 null false 23361 Kimberly Merritt 1780 Gross Forest Suite 024 1983-12-19T00:00:00Z 2018-09-14 2021-01-01 true 23362 Holly Gonzalez 255 Atkins Rapids Suite 667 1997-12-16T00:00:00Z 2014-06-12 null true 23363 Tammy Howell 4942 Chad Flats Suite 219 1999-06-13T00:00:00Z 2019-09-29 null true 23364 Brittney Rowland 15213 Lopez Heights Apt. 877 1980-07-26T00:00:00Z 2021-10-14 null true 23365 William Coleman 288 Jacob Loop 1992-09-05T00:00:00Z 2021-08-14 null true 23366 Dustin Malone 916 Annette Cliffs 2006-01-08T00:00:00Z 2020-06-11 null true 23367 Tammy Barnes 028 Chelsea Stream 1991-10-01T00:00:00Z 2017-03-01 null true 23368 Jeremiah Hendrix 9931 Perez Mall Suite 387 2002-05-27T00:00:00Z 2018-05-05 null true 23369 Lisa Taylor 34388 Miles Forest Suite 888 1989-03-05T00:00:00Z 2017-10-12 null true 23370 Jason Morrison 7747 Perez Prairie 1986-01-30T00:00:00Z 2020-05-31 null true 23371 Richard Villanueva 1432 Dennis Trace Apt. 422 2001-08-04T00:00:00Z 2016-03-04 null true 23372 Brenda Kirk 31318 Solis Path Apt. 768 1986-12-08T00:00:00Z 2022-01-08 null false 23373 Benjamin Montgomery 72142 Jennifer Hills Apt. 045 1990-03-13T00:00:00Z 2018-01-22 2021-09-01 true 23374 Tiffany Henry 34437 Michelle Path 2005-03-23T00:00:00Z 2019-05-25 null true 23375 Victoria Richard 4569 Shannon Summit 2000-08-29T00:00:00Z 2019-10-12 2021-08-01 true 23376 Kim Hunter 775 Samuel Crest 1998-10-11T00:00:00Z 2020-05-08 null false 23377 Savannah Gross 8694 Dwayne Causeway 2000-01-14T00:00:00Z 2022-01-01 null true 23378 Laura Newton 178 April Plains 2003-06-13T00:00:00Z 2020-04-06 null false 23379 Joanne Clark 3515 Norman Stravenue Suite 708 1999-02-08T00:00:00Z 2020-08-22 2020-10-01 true 23380 Brittany Stout 632 Matthew Via 1965-05-14T00:00:00Z 2020-01-07 null false 23381 Elizabeth Hampton 169 Robert Avenue 1999-11-27T00:00:00Z 2017-04-13 null true 23382 Matthew Anderson 8892 John Mountains 1988-01-03T00:00:00Z 2021-10-16 null true 23383 Janet Booker 22793 Kimberly Lodge Apt. 174 2003-10-24T00:00:00Z 2019-10-15 2020-10-01 true 23384 Brian Francis 828 Emily Greens Suite 152 2000-04-27T00:00:00Z 2020-05-27 null false 23385 Shane Williamson 61988 Heidi Knolls 1970-07-15T00:00:00Z 2019-11-30 null true 23386 Roberta Fitzpatrick 15363 Mitchell Canyon 1957-06-17T00:00:00Z 2019-11-03 2020-11-01 true 23387 Brian Taylor 51848 Cody Plains 2000-02-14T00:00:00Z 2022-01-19 null true 23388 Cindy Fuller 515 Brooke Burgs Apt. 175 1998-01-02T00:00:

trip_id rideable_type started_at ended_at start_station_id end_station_id rider_id 0FEFDE2603568365 classic_bike 2021-02-14T17:52:38Z 2021-02-14T18:12:09Z 525 16806 47854 E6159D746B2DBB91 electric_bike 2021-02-09T19:10:18Z 2021-02-09T19:19:10Z KA1503000012 TA1305000029 70870 B32D3199F1C2E75B classic_bike 2021-02-02T17:49:41Z 2021-02-02T17:54:06Z 637 TA1305000034 58974 83E463F23575F4BF electric_bike 2021-02-23T15:07:23Z 2021-02-23T15:22:37Z 13216 TA1309000055 39608 BDAA7E3494E8D545 electric_bike 2021-02-24T15:43:33Z 2021-02-24T15:49:05Z 18003 KP1705001026 36267 A772742351171257 classic_bike 2021-02-01T17:47:42Z 2021-02-01T17:48:33Z KP1705001026 KP1705001026 50104 295476889D9B79F8 classic_bike 2021-02-11T18:33:53Z 2021-02-11T18:35:09Z 18003 18003 19618 362087194BA4CC9A classic_bike 2021-02-27T15:13:39Z 2021-02-27T15:36:36Z KP1705001026 KP1705001026 16732 21630F715038CCB0 classic_bike 2021-02-20T08:59:42Z 2021-02-20T09:17:04Z KP1705001026 KP1705001026 57068 A977EB7FE7F5CD3A classic_bike 2021-02-20T08:58:16Z 2021-02-20T08:58:41Z KP1705001026 KP1705001026 32712 8B868B03D6753C2A classic_bike 2021-02-20T16:45:11Z 2021-02-20T16:59:47Z KP1705001026 KP1705001026 23227 BD331D658B9D2C31 classic_bike 2021-02-18T13:21:03Z 2021-02-18T13:25:20Z 525 520 73221 8DFEA9BAFE6BAA62 classic_bike 2021-02-26T17:40:05Z 2021-02-26T17:42:49Z 13253 TA1309000050 22163 27BE9F6E67AFD86C classic_bike 2021-02-06T14:40:25Z 2021-02-06T14:55:50Z 525 15578 7566 9B790D47A0A0F7F1 classic_bike 2021-02-19T23:25:40Z 2021-02-20T00:10:00Z KA1503000044 KA1504000142 71588 3C2DF72600B1DE6C classic_bike 2021-02-18T23:20:10Z 2021-02-19T00:01:39Z KA1503000044 KA1504000142 38661 48A8D07ED9C7065C classic_bike 2021-02-20T23:35:29Z 2021-02-21T00:17:18Z KA1503000044 KA1504000142 64751 BBFF2AAA0A3A1A26 electric_bike 2021-02-02T15:48:52Z 2021-02-02T16:03:40Z KA1504000140 17660 10721 030723CBA8CF05E7 classic_bike 2021-02-23T07:44:12Z 2021-02-23T07:48:57Z TA1305000032 15542 13281 7DF4C2D21E1DDD46 classic_bike 2021-02-09T14:00:06Z 2021-02-09T14:30:29Z 525 605 39717 2C4AF52044E874FC electric_bike 2021-02-26T18:16:25Z 2021-02-26T18:27:55Z TA1306000012 SL-007 39561 6E944BAF2AB37023 classic_bike 2021-02-24T17:09:22Z 2021-02-24T17:38:15Z 525 TA1307000144 22386 3CDFBD181A0EDB00 classic_bike 2021-02-23T11:28:45Z 2021-02-23T11:32:39Z KA1503000044 TA1307000151 9130 96F92F578CD76F59 classic_bike 2021-02-27T13:32:44Z 2021-02-27T13:32:58Z 637 637 9578 42B25557198348CC classic_bike 2021-02-23T16:05:02Z 2021-02-23T16:20:35Z 13133 13133 44811 AD6C500EEAD6B929 classic_bike 2021-02-27T16:14:45Z 2021-02-27T16:59:59Z SL-005 SL-005 5515 3158E663B4F160EB classic_bike 2021-02-27T15:38:05Z 2021-02-27T15:38:22Z 13235 13235 2437 78849DFCC4D4B7A0 classic_bike 2021-02-28T13:31:50Z 2021-02-28T14:47:14Z 13235 13235 18861 1F3946A6B0E9AC91 classic_bike 2021-02-01T15:08:37Z 2021-02-01T15:08:59Z TA1307000139 TA1307000139 42244 F6ABBD3E1BDA78A6 classic_bike 2021-02-11T11:46:46Z 2021-02-11T11:46:48Z TA1307000139 TA1307000139 53164 D5171DFF5A12AD19 classic_bike 2021-02-02T17:27:52Z 2021-02-02T17:28:28Z TA1307000139 TA1307000139 62292 BFFC6C2C4695FF77 classic_bike 2021-02-13T11:33:28Z 2021-02-13T11:44:20Z KA1503000012 13303 50851 C92659AC52A6ED41 classic_bike 2021-02-23T08:40:07Z 2021-02-23T08:43:26Z 525 KA1504000175 35044 1912C41A49F978E3 classic_bike 2021-02-10T12:43:40Z 2021-02-10T13:18:11Z TA1305000009 TA1309000025 36091 BDC123B6A30860A1 classic_bike 2021-02-27T12:47:30Z 2021-02-27T13:09:05Z TA1306000012 632 16670 E02AEC4FFF8DF297 classic_bike 2021-02-13T17:12:08Z 2021-02-13T17:38:56Z 525 523 33490 E5C4460CD39EAD34 electric_bike 2021-02-24T11:05:14Z 2021-02-24T11:21:35Z 13276 TA1306000009 26823 0CD1F34E95496D3B classic_bike 2021-02-26T17:25:00Z 2021-02-26T17:40:00Z TA1307000107 TA1309000026 24457 BC260AB096E30CB7 docked_bike 2021-02-23T18:21:39Z 2021-02-23T18:42:47Z 13276 13276 50322 F0C6DBAE926D2E27 classic_bike 2021-02-04T16:23:15Z 2021-02-04T16:29:27Z 13193 TA1307000142 34451 E3D38203A2D907DB classic_bike 2021-02-08T

station_id name latitude longitude KA1503000012 Clark St & Lake St 41.885796 -87.6311 637 Wood St & Chicago Ave 41.895634 -87.672066 13216 State St & 33rd St 41.834732 -87.625824 18003 Fairbanks St & Superior St 41.89581 -87.620255 KP1705001026 LaSalle Dr & Huron St 41.89488 -87.632324 13253 Lincoln Ave & Waveland Ave 41.948795 -87.67528 KA1503000044 Rush St & Hubbard St 41.890175 -87.62618 KA1504000140 Winchester Ave & Elston Ave 41.924038 -87.676414 TA1305000032 Clinton St & Madison St 41.88224 -87.64107 TA1306000012 Wells St & Huron St 41.894753 -87.6344 13133 Damen Ave & Cortland St 41.91598 -87.67734 SL-005 Indiana Ave & Roosevelt Rd 41.86789 -87.62304 13235 Southport Ave & Waveland Ave 41.94815 -87.66394 TA1307000139 MLK Jr Dr & 29th St 41.842052 -87.617 TA1305000009 Clark St & Ida B Wells Dr 41.87593 -87.630585 13276 Stockton Dr & Wrightwood Ave 41.931347 -87.638695 TA1307000107 Sheridan Rd & Montrose Ave 41.96167 -87.65464 13193 Larrabee St & Webster Ave 41.92182 -87.64414 KA1503000072 Wacker Dr & Washington St 41.883133 -87.63732 TA1307000166 Halsted St & Willow St 41.913864 -87.64876 13285 Wood St & Taylor St (Temp) 41.869267 -87.67373 TA1306000016 Sheffield Ave & Fullerton Ave 41.925526 -87.65369 13303 Clark St & Chicago Ave 41.89675 -87.63089 15575 Broadway & Thorndale Ave 41.989742 -87.66014 623 Michigan Ave & 8th St 41.872288 -87.62392 TA1309000050 Lincoln Ave & Addison St 41.946175 -87.67331 15445 Wentworth Ave & 33rd St 41.83453 -87.63182 13164 Racine Ave & 18th St 41.858166 -87.656494 TA1307000151 Wells St & Hubbard St 41.889908 -87.63427 13158 Peoria St & Jackson Blvd 41.87764 -87.64962 13150 Michigan Ave & 18th St 41.857815 -87.62455 TA1308000036 Indiana Ave & 31st St 41.838844 -87.62184 TA1308000013 Halsted St & Archer Ave 41.847202 -87.6468 TA1306000013 New St & Illinois St 41.890846 -87.618614 13061 Ashland Ave & Division St 41.90345 -87.66775 TA1307000048 Fort Dearborn Dr & 31st St 41.838554 -87.608215 TA1308000045 Wallace St & 35th St 41.830627 -87.64129 13206 Loomis St & Jackson Blvd 41.877945 -87.66201 13156 Aberdeen St & Monroe St 41.88042 -87.65552 TA1306000015 Morgan St & Lake St 41.885483 -87.652306 13058 Dayton St & North Ave 41.91058 -87.64942 TA1309000008 Franklin St & Adams St (Temp) 41.879433 -87.635506 KA1504000135 Wells St & Elm St 41.903206 -87.63461 KA1503000064 Dusable Harbor 41.886974 -87.612816 TA1305000022 Orleans St & Merchandise Mart Plaza 41.888245 -87.63639 KA1504000079 Larrabee St & Division St 41.903484 -87.64336 KA1503000022 Clark St & Montrose Ave 41.96159 -87.66604 13109 Broadway & Berwyn Ave 41.97835 -87.65975 15530 Rush St & Superior St 41.895763 -87.62591 TA1306000010 Daley Center Plaza 41.88424 -87.62963 13146 Clark St & Armitage Ave 41.918304 -87.636284 15578 Broadway & Ridge Ave 41.984043 -87.66027 KA1503000034 LaSalle St & Adams St 41.879345 -87.63199 KA1503000059 Lake Park Ave & 53rd St 41.799496 -87.58645 TA1305000011 Michigan Ave & Lake St 41.886024 -87.624115 TA1307000061 State St & Pearson St 41.89745 -87.62872 SL-011 Wells St & Polk St 41.872597 -87.6335 TA1309000010 Wabash Ave & 9th St 41.870262 -87.62538 15534 Field Blvd & South Water St 41.88635 -87.617516 TA1307000119 Clarendon Ave & Leland Ave 41.967968 -87.65 TA1305000029 State St & Randolph St 41.88473 -87.62773 TA1309000063 Lake Park Ave & 56th St 41.793243 -87.58778 KA1504000133 Rush St & Cedar St 41.90231 -87.62769 624 Dearborn St & Van Buren St 41.876194 -87.62913 KA1503000029 South Shore Dr & 67th St 41.773643 -87.56751 13323 Broadway & Sheridan Rd 41.95283 -87.649994 KA1504000149 Damen Ave & Foster Ave 41.975616 -87.67946 TA1309000004 LaSalle St & Jackson Blvd 41.878166 -87.63193 18058 Leavitt St & Chicago Ave 41.895435 -87.681984 WL-008 Clinton St & Roosevelt Rd 41.867054 -87.64109 13221 Wood St & Milwaukee Ave 41.907654 -87.672554 523 Eastlake Ter & Rogers Ave 42.020885 -87.665054 TA1309000025 Halsted St & Roscoe St 41.94367 -87.64895 13288 Damen Ave & Charleston St 41.92008 -87.67795 658 Leavitt S

payment_id date amount rider_id 1496876 2020-04-01T00:00:00Z 9.0 58830 1496877 2020-05-01T00:00:00Z 9.0 58830 1496878 2020-06-01T00:00:00Z 9.0 58830 1496879 2020-07-01T00:00:00Z 9.0 58830 1496880 2020-08-01T00:00:00Z 9.0 58830 1496881 2020-09-01T00:00:00Z 9.0 58830 1496882 2020-10-01T00:00:00Z 9.0 58830 1496883 2020-11-01T00:00:00Z 9.0 58830 1496884 2020-12-01T00:00:00Z 9.0 58830 1496885 2021-01-01T00:00:00Z 9.0 58830 1496886 2021-02-01T00:00:00Z 9.0 58830 1496887 2021-03-01T00:00:00Z 9.0 58830 1496888 2021-04-01T00:00:00Z 9.0 58830 1496889 2021-05-01T00:00:00Z 9.0 58830 1496890 2021-06-01T00:00:00Z 9.0 58830 1496891 2021-07-01T00:00:00Z 9.0 58830 1496892 2021-08-01T00:00:00Z 9.0 58830 1496893 2021-09-01T00:00:00Z 9.0 58830 1496894 2021-10-01T00:00:00Z 9.0 58830 1496895 2021-11-01T00:00:00Z 9.0 58830 1496896 2021-12-01T00:00:00Z 9.0 58830 1496897 2022-01-01T00:00:00Z 9.0 58830 1496898 2022-02-01T00:00:00Z 9.0 58830 1496899 2021-02-01T00:00:00Z 9.0 58831 1496900 2021-03-01T00:00:00Z 9.0 58831 1496901 2021-04-01T00:00:00Z 9.0 58831 1496902 2021-05-01T00:00:00Z 9.0 58831 1496903 2021-06-01T00:00:00Z 9.0 58831 1496904 2021-07-01T00:00:00Z 9.0 58831 1496905 2021-08-01T00:00:00Z 9.0 58831 1496906 2021-06-01T00:00:00Z 9.0 58832 1496907 2021-07-01T00:00:00Z 9.0 58832 1496908 2021-08-01T00:00:00Z 9.0 58832 1496909 2021-09-01T00:00:00Z 9.0 58832 1496910 2021-10-01T00:00:00Z 9.0 58832 1496911 2021-11-01T00:00:00Z 9.0 58832 1496912 2021-12-01T00:00:00Z 9.0 58832 1496913 2022-01-01T00:00:00Z 9.0 58832 1496914 2022-02-01T00:00:00Z 9.0 58832 1496915 2017-09-01T00:00:00Z 9.0 58833 1496916 2017-10-01T00:00:00Z 9.0 58833 1496917 2017-11-01T00:00:00Z 9.0 58833 1496918 2017-12-01T00:00:00Z 9.0 58833 1496919 2018-01-01T00:00:00Z 9.0 58833 1496920 2018-02-01T00:00:00Z 9.0 58833 1496921 2018-03-01T00:00:00Z 9.0 58833 1496922 2018-04-01T00:00:00Z 9.0 58833 1496923 2018-05-01T00:00:00Z 9.0 58833 1496924 2018-06-01T00:00:00Z 9.0 58833 1496925 2018-07-01T00:00:00Z 9.0 58833 1496926 2018-08-01T00:00:00Z 9.0 58833 1496927 2018-09-01T00:00:00Z 9.0 58833 1496928 2018-10-01T00:00:00Z 9.0 58833 1496929 2018-11-01T00:00:00Z 9.0 58833 1496930 2018-12-01T00:00:00Z 9.0 58833 1496931 2019-01-01T00:00:00Z 9.0 58833 1496932 2019-02-01T00:00:00Z 9.0 58833 1496933 2019-03-01T00:00:00Z 9.0 58833 1496934 2019-04-01T00:00:00Z 9.0 58833 1496935 2019-05-01T00:00:00Z 9.0 58833 1496936 2019-06-01T00:00:00Z 9.0 58833 1496937 2019-07-01T00:00:00Z 9.0 58833 1496938 2019-08-01T00:00:00Z 9.0 58833 1496939 2019-09-01T00:00:00Z 9.0 58833 1496940 2019-10-01T00:00:00Z 9.0 58833 1496941 2019-11-01T00:00:00Z 9.0 58833 1496942 2019-12-01T00:00:00Z 9.0 58833 1496943 2020-01-01T00:00:00Z 9.0 58833 1496944 2020-02-01T00:00:00Z 9.0 58833 1496945 2020-03-01T00:00:00Z 9.0 58833 1496946 2020-04-01T00:00:00Z 9.0 58833 1496947 2020-05-01T00:00:00Z 9.0 58833 1496948 2020-06-01T00:00:00Z 9.0 58833 1496949 2020-07-01T00:00:00Z 9.0 58833 1496950 2020-08-01T00:00:00Z 9.0 58833 1496951 2020-09-01T00:00:00Z 9.0 58833 1496952 2020-10-01T00:00:00Z 9.0 58833 1496953 2020-11-01T00:00:00Z 9.0 58833 1496954 2020-12-01T00:00:00Z 9.0 58833 1496955 2021-01-01T00:00:00Z 9.0 58833 1496956 2021-02-01T00:00:00Z 9.0 58833 1496957 2021-03-01T00:00:00Z 9.0 58833 1496958 2021-04-01T00:00:00Z 9.0 58833 1496959 2021-05-01T00:00:00Z 9.0 58833 1496960 2021-06-01T00:00:00Z 9.0 58833 1496961 2021-07-01T00:00:00Z 9.0 58833 1496962 2021-08-01T00:00:00Z 9.0 58833 1496963 2021-09-01T00:00:00Z 9.0 58833 1496964 2021-10-01T00:00:00Z 9.0 58833 1496965 2021-11-01T00:00:00Z 9.0 58833 1496966 2021-12-01T00:00:00Z 9.0 58833 1496967 2022-01-01T00:00:00Z 9.0 58833 1496968 2022-02-01T00:00:00Z 9.0 58833 1496969 2013-08-01T00:00:00Z 9.0 58834 1496970 2013-09-01T00:00:00Z 9.0 58834 1496971 2013-10-01T00:00:00Z 9.0 58834 1496972 2013-11-01T00:00:00Z 9.0 58834 1496973 2013-12-01T00:00:00Z 9.0 58834 1496974 2014-01-01T00:00:00Z 9.0 58834 1496975 2014-02-01T00:00:00Z 9.0 58834 1496976 2014-03-01T00:00:00Z 9.0 58834 1496977 2014-04-01T00:00:00Z 

## 2. Staging Step  `Silver Layer`
The **staging step** is where we prepare the raw ingested data for transformations.  

In [0]:
from pyspark.sql.functions import col, to_date, datediff

# -------- Riders --------
df_rider_bronze = spark.read.format("delta").load("/deltaLake/bronze/rider")

df_rider_silver = (
    df_rider_bronze
    .dropDuplicates(["rider_id"])
    .filter(col("rider_id").isNotNull())
    .withColumnRenamed("birthday", "birth_date")
)

df_rider_silver.write.format("delta").mode("overwrite").save("/deltaLake/silver/rider")


# -------- Stations --------
df_station_bronze = spark.read.format("delta").load("/deltaLake/bronze/station")

df_station_silver = (
    df_station_bronze
    .dropDuplicates(["station_id"])
    .filter(col("station_id").isNotNull())
)

df_station_silver.write.format("delta").mode("overwrite").save("/deltaLake/silver/station")


# -------- Trips --------
df_trip_bronze = spark.read.format("delta").load("/deltaLake/bronze/trip")

df_trip_silver = (
    df_trip_bronze
    .dropDuplicates(["trip_id"])
    .filter((col("rider_id").isNotNull()))
)

df_trip_silver.write.format("delta").mode("overwrite").save("/deltaLake/silver/trip")


# -------- Payments --------
df_payment_bronze = spark.read.format("delta").load("/deltaLake/bronze/payment")

df_payment_silver = (
    df_payment_bronze
    .dropDuplicates(["payment_id"])
    .filter((col("rider_id").isNotNull()) & (col("amount").isNotNull()))
    .withColumn("amount", col("amount").cast("double"))
    .withColumnRenamed("date","payment_date")
)

df_payment_silver.write.format("delta").mode("overwrite").save("/deltaLake/silver/payment")


## The Star Schema `Gold Layer`
it’s been ingested, cleaned, conformed, and aggregated so it is reliable, and tailored for analytical needs. 

In [0]:
from pyspark.sql.functions import *


# ----------------------- silver layer DataFrames loaded -------------------
df_rider_silver = spark.read.format("delta").load("/deltaLake/silver/rider")
df_trip_silver = spark.read.format("delta").load("/deltaLake/silver/trip")
df_station_silver = spark.read.format("delta").load("/deltaLake/silver/station")
df_payment_silver = spark.read.format("delta").load("/deltaLake/silver/payment")


# Gather all dates
all_dates = df_payment_silver.select(col("payment_date").alias("full_date")) \
            .union(df_trip_silver.select(col("started_at").alias("full_date"))) \
            .union(df_trip_silver.select(col("ended_at").alias("full_date"))) \
            .filter(col("full_date").isNotNull()) \
            .distinct()

# dim_date
dim_date = all_dates \
            .withColumn("date_id", date_format(col("full_date"), "yyyyMMdd").cast("int")) \
            .withColumn("date", date_format(col("full_date"), ")")) \
            .withColumn("FullDateTime", to_timestamp(col("full_date"), "yyyy-MM-dd HH:mm:ss")) \
            .withColumn("year", year(col("full_date"))) \
            .withColumn("quarter", quarter(col("full_date"))) \
            .withColumn("month", month(col("full_date"))) \
            .withColumn("month_name", date_format(col("full_date"), "MMMM")) \
            .withColumn("day", dayofmonth(col("full_date"))) \
            .withColumn("day_name", date_format(col("full_date"), "EEEE")) \
            .orderBy("full_date")

# Save to gold layer
dim_date.write.format("delta").mode("overwrite").save("/deltaLake/gold/dim_date")

# dim_station
dim_station = df_station_silver.select("station_id", "name", "latitude", "longitude")

dim_station.write.format("delta").mode("overwrite").save("/deltaLake/gold/dim_station")

# dim_rider
dim_rider = df_rider_silver.select("rider_id", "first_name", "last_name", "address", "birth_date", "account_start_date", "account_end_date", "is_member")

dim_rider.write.format("delta").mode("overwrite").save("/deltaLake/gold/dim_rider")

# fact_payment
fact_payment = df_payment_silver \
               .join(dim_date,df_payment_silver["payment_date"] == dim_date["FullDateTime"], "inner") \
               .join(df_rider_silver, "rider_id" , "inner") \
               .select(
                   df_payment_silver["payment_id"],
                   dim_date["date_id"].alias("date_id"),
                   df_payment_silver["amount"],
                   df_rider_silver["rider_id"]
                   )

fact_payment.write.format("delta").mode("overwrite").save("/deltaLake/gold/fact_payment")

#  fact_trip
fact_trip = df_trip_silver \
    .join(dim_date.alias("d1"), df_trip_silver["started_at"] == col("d1.FullDateTime"), "inner") \
    .join(dim_date.alias("d2"), df_trip_silver["ended_at"] == col("d2.FullDateTime"), "inner") \
    .join(dim_station.alias("s1"), df_trip_silver["start_station_id"] == col("s1.station_id"), "inner") \
    .join(dim_station.alias("s2"), df_trip_silver["end_station_id"] == col("s2.station_id"), "inner") \
    .join(df_rider_silver, "rider_id", "inner") \
    .select(
        df_trip_silver["trip_id"],
        col("d1.date_id").alias("start_date_id"),
        col("d2.date_id").alias("end_date_id"),
        col("s1.station_id").alias("start_station_id"),
        col("s2.station_id").alias("end_station_id"),
        df_rider_silver["rider_id"],
        df_trip_silver["rideable_type"],
        df_trip_silver["started_at"],
        df_trip_silver["ended_at"],
        df_rider_silver["birth_date"]
    ) \
    .withColumn("trip_duration", round((unix_timestamp(col("ended_at")) - unix_timestamp(col("started_at"))) / 60)) \
    .withColumn("rider_age", floor(months_between(col("started_at"), col("birth_date")) / 12))

fact_trip.write.format("delta").mode("overwrite").save("/deltaLake/gold/fact_trip")


# Gold Layer - Convert to saveAsTable()

# Dimension tables
dim_rider.write.format("delta").mode("overwrite").saveAsTable("dim_rider")
dim_station.write.format("delta").mode("overwrite").saveAsTable("dim_station") 
dim_date.write.format("delta").mode("overwrite").saveAsTable("dim_date")

# Fact tables
fact_trip.write.format("delta").mode("overwrite").saveAsTable("fact_trip")
fact_payment.write.format("delta").mode("overwrite").saveAsTable("fact_payment")

